In [12]:
# conda install scikit-learn
# install from: http://docs.python-requests.org/en/master/
# to fix ssl installation of python packages issue
# curl https://bootstrap.pypa.io/get-pip.py | python3
# instructions to setup virtualenv
# https://www.tensorflow.org/install/install_mac
# pip3 install -r requirements.txt
# https://www.datacamp.com/community/tutorials/tensorflow-tutorial
# https://github.com/jtopor/CUNY-MSDA-661/blob/master/CIFAR-100/TF-Layers-CIFAR-100-v2.py
# feature columns
# https://data-flair.training/blogs/tensorflow-wide-and-deep-learning/

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import requests
import cv2
import h5py
import scipy.misc
import numpy as np
import csv
import sklearn.model_selection as model
import pickle 
import tensorflow as tf

from csv import DictReader
from urllib.request import urlopen
from matplotlib.pyplot import imshow
from fr_utils import *
from inception_blocks_v2 import *
from skimage import transform
from tensorflow.contrib import learn
from tensorflow.contrib.learn.python.learn.estimators import model_fn as model_fn_lib

%matplotlib inline
%load_ext autoreload
%autoreload

learning_rate = 0.001
IMAGE_HEIGHT = 32
IMAGE_WIDTH = 32
IMAGE_DEPTH = 3

np.set_printoptions(threshold=np.nan)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [13]:
def convert_input_format(data):    
    return np.transpose(
        np.reshape(data, (-1, 32, 32, 3), order="F"),
        axes=(0, 2, 1, 3)
    )

def convert_output_labels(data):
    return np.asarray(data['fine_labels'], dtype=np.int32)

def one_hot_labels(labels):
    return tf.one_hot(indices=tf.cast(labels, tf.int32), depth=100)

def unpickle(file):
    fo = open(file, "rb")
    dict = pickle.load(fo, encoding="latin1")
    fo.close()
    return dict

In [14]:
def conv_layer(input_layer, filters=32, kernel_size=[5,5]):
    # setting up the conv layer, with stride and padding
    return tf.layers.conv2d(
        inputs=input_layer,
        filters=filters,
        kernel_size=kernel_size,
        padding="same",
        activation=tf.nn.relu
    )

def maxpool_layer(conv, pool_size=[2,2], strides=2):
    return tf.layers.max_pooling2d(
        inputs=conv, pool_size=pool_size, strides=strides
    )

def dropout_layer(inputs, mode, rate=0.25):
    
    return tf.layers.dropout(
        inputs=inputs, rate=rate, training=mode == learn.ModeKeys.TRAIN
    )

def dense_layer(inputs, units, activation=tf.nn.relu):
    return tf.layers.dense(inputs=inputs, units=units, activation=activation)

def determine_loss(labels, logits, mode):
    print(mode)
#     if mode != learn.ModeKeys.INFER:
    return tf.losses.softmax_cross_entropy (
        onehot_labels=one_hot_labels(labels),
        logits=logits
    )
#     else:
#         return None
    
def determine_train_op(loss, mode):
    print(mode)
#     if mode == learn.ModeKeys.TRAIN:
    return tf.contrib.layers.optimize_loss (
        loss=loss, 
        global_step=tf.contrib.framework.get_global_step(),
        learning_rate=0.0001,
        optimizer="Adam"
    )
#     else:
#         return None
    
def generate_predictions(logits):
    return {
        "classes": tf.argmax(input=logits, axis=1),
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }

def cnn_model(features, labels, mode): 
    mode = learn.ModeKeys.TRAIN if mode == "train" else learn.ModeKeys.INFER
    input_layer = tf.convert_to_tensor(features)
    
    # cnn layer 1
    conv1 = conv_layer(input_layer)
    conv2 = conv_layer(conv1)
    
    # pooling layer 1 
    pool1 = maxpool_layer(conv2)
    
    # dropout operation
    dropout1 = dropout_layer(pool1, mode)
    
    # cnn layer 2 
    conv3 = conv_layer(dropout1, 64, [3, 3])
    conv4 = conv_layer(conv3, 64, [3, 3])
    
    # pooling layer 2
    pool2 = maxpool_layer(conv4)
    
    # dropout operation
    dropout2 = dropout_layer(pool2, mode)
    
    # flatten tensor into a batch of vectors
    pool2_flat = tf.reshape(dropout2, [-1, 8 * 8 * 64])
    
    # dense layer 
    dense1 = dense_layer(pool2_flat, 1024)
    
    # flatten tensor again
    dropout3 = dropout_layer(dense1, mode, 0.4)
    
    # second fully connected layer 
    dense2 = tf.layers.dense(inputs=dropout3, units=512)
    
    # dropout operation
    dropout4 = dropout_layer(dense2, mode, 0.4)
    
    # logits layer
    logits = tf.layers.dense(inputs=dropout4, units=100)
    
    loss = determine_loss(labels, logits, mode)
    train_op = determine_train_op(loss, mode)
    predictions = generate_predictions(logits)
    
    return model_fn_lib.ModelFnOps(
        mode=mode, predictions=predictions, loss=loss, train_op=train_op
    )


In [16]:
def generate_accuracy_metric():
    # configure the accuracy metric
    return {
        "accuracy": learn.MetricSpec (
            metric_fn=tf.metrics.accuracy, prediction_key="classes"
        )
    }

def serving_input_fn():
    """An input receiver that expects a serialized tf.Example."""

    # feature spec dictionary  determines our input parameters for the model
    feature_spec = {
        'images': tf.FixedLenFeature(shape=[1], dtype=tf.float32)
    }

    # the inputs will be initially fed as strings with data serialized by
    # Google ProtoBuffers
    serialized_tf_example = tf.placeholder(
        dtype=tf.string, shape=[1], name='input_example_tensor')
    receiver_tensors = {'images': serialized_tf_example}

    # deserialize input
    features = tf.parse_example(serialized_tf_example, feature_spec)
    return tf.estimator.export.ServingInputReceiver(features, receiver_tensors)
    
def print_evaluate_model(cifar_classifier, data, labels, epoches, subset):
    small_train = np.array_split(data, epoches)[subset]
    small_labels = np.array_split(labels, epoches)[subset]
    evaluate_results = cifar_classifier.evaluate(
        x=small_train, y=small_labels, metrics=generate_accuracy_metric()
    )
    print(evaluate_results)
    return evaluate_results

def setup_and_train_model():
    dataset = unpickle("./datasets/cifar-100-parsed/cifar-100-python/train")
    data = dataset["data"]
    data = data.astype("float32")
    train_data = convert_input_format(data)
    train_labels = convert_output_labels(dataset)
    model_ckpt = "/tmp/cifar100"
    
    deep_columns = [
        tf.feature_column.numeric_column('beaver'),
        tf.feature_column.numeric_column('dolphin'),
        tf.feature_column.numeric_column('otter'),
        tf.feature_column.numeric_column('seal'),
        tf.feature_column.numeric_column('whale'),
        tf.feature_column.numeric_column('aquarium fish'),
        tf.feature_column.numeric_column('flatfish'),
        tf.feature_column.numeric_column('ray'),
        tf.feature_column.numeric_column('shark'),
        tf.feature_column.numeric_column('trout'),
        tf.feature_column.numeric_column('orchids'),
        tf.feature_column.numeric_column('poppies'),
        tf.feature_column.numeric_column('roses'),
        tf.feature_column.numeric_column('sunflowers'),
        tf.feature_column.numeric_column('sunflowers'),
        tf.feature_column.numeric_column('bottles'),
        tf.feature_column.numeric_column('bowls'),
        tf.feature_column.numeric_column('cans'),
        tf.feature_column.numeric_column('cups'),
        tf.feature_column.numeric_column('plates'),
        tf.feature_column.numeric_column('apples'),
        tf.feature_column.numeric_column('mushrooms'),
        tf.feature_column.numeric_column('oranges'),
        tf.feature_column.numeric_column('pears'),
        tf.feature_column.numeric_column('sweet peppers'),
        tf.feature_column.numeric_column('clock'),
        tf.feature_column.numeric_column('computer keyboard'),
        tf.feature_column.numeric_column('lamp'),
        tf.feature_column.numeric_column('telephone'),
        tf.feature_column.numeric_column('television'),
        tf.feature_column.numeric_column('bed'),
        tf.feature_column.numeric_column('chair'),
        tf.feature_column.numeric_column('couch'),
        tf.feature_column.numeric_column('table'),
        tf.feature_column.numeric_column('wardrobe'),
        tf.feature_column.numeric_column('bee'),
        tf.feature_column.numeric_column('beetle'),
        tf.feature_column.numeric_column('butterfly'),
        tf.feature_column.numeric_column('caterpillar'),
        tf.feature_column.numeric_column('cockroach'),
        tf.feature_column.numeric_column('bear'),
        tf.feature_column.numeric_column('leopard'),
        tf.feature_column.numeric_column('lion'),
        tf.feature_column.numeric_column('tiger'),
        tf.feature_column.numeric_column('wolf'),
        tf.feature_column.numeric_column('bridge'),
        tf.feature_column.numeric_column('castle'),
        tf.feature_column.numeric_column('house'),
        tf.feature_column.numeric_column('road'),
        tf.feature_column.numeric_column('skyscraper'),
        tf.feature_column.numeric_column('cloud'),
        tf.feature_column.numeric_column('forest'),
        tf.feature_column.numeric_column('mountain'),
        tf.feature_column.numeric_column('plain'),
        tf.feature_column.numeric_column('sea'),
        tf.feature_column.numeric_column('camel'),
        tf.feature_column.numeric_column('cattle'),
        tf.feature_column.numeric_column('chimpanzee'),
        tf.feature_column.numeric_column('elephant'),
        tf.feature_column.numeric_column('kangaroo'),
        tf.feature_column.numeric_column('fox'),
        tf.feature_column.numeric_column('porcupine'),
        tf.feature_column.numeric_column('possum'),
        tf.feature_column.numeric_column('raccoon'),
        tf.feature_column.numeric_column('skunk'),
        tf.feature_column.numeric_column('crab'),
        tf.feature_column.numeric_column('lobster'),
        tf.feature_column.numeric_column('snail'),
        tf.feature_column.numeric_column('spider'),
        tf.feature_column.numeric_column('worm'),
        tf.feature_column.numeric_column('baby'),
        tf.feature_column.numeric_column('boy'),
        tf.feature_column.numeric_column('girl'),
        tf.feature_column.numeric_column('man'),
        tf.feature_column.numeric_column('woman'),
        tf.feature_column.numeric_column('crocodile'),
        tf.feature_column.numeric_column('dinosaur'),
        tf.feature_column.numeric_column('lizard'),
        tf.feature_column.numeric_column('snake'),
        tf.feature_column.numeric_column('turtle'),
        tf.feature_column.numeric_column('hamster'),
        tf.feature_column.numeric_column('mouse'),
        tf.feature_column.numeric_column('rabbit'),
        tf.feature_column.numeric_column('shrew'),
        tf.feature_column.numeric_column('squirrel'),
        tf.feature_column.numeric_column('maple'),
        tf.feature_column.numeric_column('oak'),
        tf.feature_column.numeric_column('palm'),
        tf.feature_column.numeric_column('pine'),
        tf.feature_column.numeric_column('willow'),
        tf.feature_column.numeric_column('bicycle'),
        tf.feature_column.numeric_column('bus'),
        tf.feature_column.numeric_column('motorcycle'),
        tf.feature_column.numeric_column('pickup truck'),
        tf.feature_column.numeric_column('train'),
        tf.feature_column.numeric_column('lawn-mower'),
        tf.feature_column.numeric_column('rocket'),
        tf.feature_column.numeric_column('streetcar'),
        tf.feature_column.numeric_column('tank'),
        tf.feature_column.numeric_column('tractor')
    ]
    
    feature_spec = tf.feature_column.make_parse_example_spec(deep_columns)
    export_input_fn = tf.contrib.learn.build_parsing_serving_input_fn(feature_spec)
    
#     exporter = tf.estimator.LatestExporter (
#         name="Servo",
#         serving_input_receiver_fn=serving_input_fn,
#         assets_extra=None,
#         as_text=False,
#         exports_to_keep=5
#     )
    
    # create custom estimator
    cifar_classifier = learn.Estimator (
        model_fn=cnn_model, model_dir="/tmp/cifar100" 
    )
    
    # log predictions
    tensors_to_log = {"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook (
        tensors=tensors_to_log, every_n_iter=100
    )
    
    # train the model
    with tf.device("/cpu:0"):
        cifar_classifier.fit (
            x=train_data,
            y=train_labels,
            batch_size=64, 
            steps=5240,
            monitors=[logging_hook]
        )
    
    full_model_dir = cifar_classifier.export_savedmodel(
        "./models/cifar-100", export_input_fn
    )
    return cifar_classifier


def test_model(cifar_classifier):
    dataset = unpickle("./datasets/cifar-100-parsed/cifar-100-python/test")
    data = dataset["data"]
    data = data.astype("float32")
    test_data = convert_input_format(data)
    test_labels = convert_output_labels(dataset)
    
    # evaluate all test data and print results
    acc = 0
    e_loss = 0
    n_batches = 20
    for i in range (0, n_batches - 1):
        small_eval =  np.array_split(test_data, n_batches)[i]
        small_labs =  np.array_split(test_labels, n_batches)[i]
        eval_results = cifar_classifier.evaluate(
          x=small_eval, y=small_labs, metrics=generate_accuracy_metric())
        print(eval_results)
        acc += eval_results["accuracy"]
        e_loss += eval_results["loss"]

    overall_acc = acc / n_batches
    overall_loss = e_loss/ n_batches
    print("Eval Accuracy = ", overall_acc)
    print("Eval Loss = ", overall_loss) 

In [17]:
classifier = setup_and_train_model()

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_num_worker_replicas': 0, '_task_type': None, '_save_summary_steps': 100, '_environment': 'local', '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x1c520fe48>, '_device_fn': None, '_session_config': None, '_task_id': 0, '_is_chief': True, '_tf_config': gpu_options {
  per_process_gpu_memory_fraction: 1.0
}
, '_save_checkpoints_secs': 600, '_save_checkpoints_steps': None, '_model_dir': '/tmp/cifar100', '_train_distribute': None, '_num_ps_replicas': 0, '_keep_checkpoint_every_n_hours': 10000, '_master': '', '_evaluation_master': '', '_keep_checkpoint_max': 5, '_log_step_count_steps': 100, '_tf_random_seed': None}
Instructions for updating:
Estimator is decoupled from Scikit Learn interface by moving into
separate class SKCompat. Arguments x, y and batch_size are only
available in the SKCompat class, Estimator will only accept input_fn.
Example conversion:
  est = Estimator(...) -> est = S

INFO:tensorflow:loss = 172.98259, step = 1
INFO:tensorflow:global_step/sec: 2.59882
INFO:tensorflow:probabilities = [[0.01470238 0.00926433 0.01361543 0.00520986 0.01092386 0.01532985
  0.00689768 0.01423841 0.00892998 0.01317784 0.00904749 0.01701432
  0.01108838 0.0113256  0.00981796 0.00669019 0.00901567 0.00755848
  0.00935357 0.00692773 0.01719916 0.00956905 0.00525331 0.01109009
  0.0096772  0.00959215 0.0174037  0.01467472 0.00797631 0.01244048
  0.00642352 0.01280413 0.00521162 0.01218947 0.00759749 0.00757881
  0.00541724 0.01179061 0.00857534 0.00508445 0.0140919  0.01297894
  0.01164064 0.00862932 0.00803169 0.00586385 0.01202601 0.00509368
  0.00592381 0.01053942 0.0122652  0.01302207 0.00654857 0.02821989
  0.00449605 0.01070076 0.01112988 0.0149267  0.01218198 0.00796465
  0.00503544 0.00758027 0.00538241 0.00879657 0.00913982 0.00612791
  0.0081899  0.01069829 0.00716005 0.00993941 0.00781941 0.01980643
  0.01318987 0.01078158 0.00917372 0.00665698 0.00841895 0.00825126


INFO:tensorflow:loss = 4.740937, step = 101 (38.483 sec)
INFO:tensorflow:global_step/sec: 2.72091
INFO:tensorflow:probabilities = [[0.00557852 0.0125814  0.00610585 0.00543545 0.01542608 0.01217118
  0.01027805 0.00564552 0.00740323 0.0102595  0.00808025 0.01009442
  0.00734185 0.01100004 0.00857823 0.01072079 0.01904292 0.00684241
  0.00926721 0.0147433  0.00906971 0.00933819 0.0096306  0.00867444
  0.01346959 0.00589419 0.01094738 0.00877468 0.00623687 0.00580666
  0.01159268 0.00812367 0.01250106 0.01044606 0.00907903 0.00958643
  0.00862876 0.00818793 0.00854967 0.00762506 0.00778762 0.00919044
  0.00803916 0.01019032 0.00963917 0.00983837 0.01170148 0.01069521
  0.00778348 0.00603623 0.01270858 0.00738103 0.00785883 0.01234849
  0.00751311 0.00702672 0.01183731 0.0095741  0.00994083 0.0110684
  0.00977913 0.00617655 0.01422368 0.01861477 0.00833514 0.01171061
  0.0067169  0.00920976 0.00724932 0.00848641 0.00970723 0.00974093
  0.003788   0.01032094 0.01451741 0.00964847 0.0103569

INFO:tensorflow:loss = 4.697071, step = 201 (36.754 sec)
INFO:tensorflow:global_step/sec: 2.75335
INFO:tensorflow:probabilities = [[0.00984614 0.00443201 0.00887418 0.00725277 0.00609669 0.00911604
  0.00966546 0.00892821 0.01012628 0.01048199 0.00968811 0.01213111
  0.01736105 0.01210586 0.01120387 0.01820215 0.00879929 0.01506846
  0.01410318 0.00833324 0.00770704 0.00776917 0.01118481 0.01853593
  0.00776443 0.01078545 0.0071807  0.00906406 0.00903416 0.01257755
  0.00852476 0.01178675 0.00916499 0.0086037  0.00599876 0.00597754
  0.00845153 0.00793769 0.01003223 0.00855016 0.01088692 0.00645751
  0.00711922 0.00466497 0.00984727 0.010477   0.01646639 0.01331379
  0.00638049 0.01136342 0.00886007 0.01486713 0.01443958 0.01417821
  0.01226772 0.00793055 0.02048552 0.00603558 0.01217068 0.00800188
  0.00776724 0.00794022 0.00548636 0.00631002 0.00561081 0.00537852
  0.00577114 0.00741504 0.00869776 0.01213373 0.0080692  0.01040496
  0.00809206 0.01634471 0.01066308 0.02092956 0.012057

INFO:tensorflow:loss = 4.6219864, step = 301 (36.319 sec)
INFO:tensorflow:global_step/sec: 2.74701
INFO:tensorflow:probabilities = [[0.00646228 0.01174982 0.0134213  0.0135912  0.00700027 0.01124759
  0.00815175 0.00993846 0.00795017 0.01320161 0.00988544 0.0153555
  0.00892037 0.01347327 0.00905488 0.01117723 0.00791743 0.01129215
  0.00723702 0.01096071 0.00967486 0.00744592 0.00628639 0.01576738
  0.01017439 0.0067957  0.00717502 0.00820561 0.01286241 0.00643461
  0.01847373 0.01461254 0.01486825 0.00717417 0.00783468 0.0067591
  0.00924495 0.00901053 0.01054647 0.01414877 0.0145457  0.00972658
  0.00622696 0.01012953 0.00946207 0.00885764 0.00479838 0.00833732
  0.00714099 0.01159021 0.00850429 0.01218843 0.00990723 0.00702874
  0.01281587 0.01270524 0.00957312 0.01092432 0.01303796 0.00830771
  0.01639846 0.00726473 0.01236829 0.00707346 0.00852352 0.00934933
  0.00738123 0.00721922 0.0083613  0.00992865 0.00761043 0.00790672
  0.00833227 0.01699517 0.00935945 0.00825962 0.0100443

...

INFO:tensorflow:loss = 3.7152703, step = 4901 (49.174 sec)
INFO:tensorflow:global_step/sec: 2.25109
INFO:tensorflow:probabilities = [[0.00003995 0.00018896 0.00040172 0.00220971 0.00024706 0.000225
  0.00006037 0.00013085 0.0004645  0.00029993 0.00083277 0.00005122
  0.00172443 0.00041541 0.00020274 0.00013163 0.00015497 0.00029916
  0.00017558 0.00009859 0.00016783 0.00021488 0.0000992  0.01300695
  0.00096934 0.00006197 0.00003984 0.00072326 0.00211856 0.00022408
  0.40435407 0.00011302 0.00097333 0.00082279 0.00046256 0.00005066
  0.00010819 0.00018805 0.00019903 0.05512249 0.00272453 0.00016412
  0.00003248 0.00022393 0.00082174 0.00018013 0.0000624  0.00004623
  0.00017086 0.00781323 0.00282358 0.00034917 0.00010845 0.0002092
  0.00022068 0.00314119 0.00063634 0.00011372 0.00009149 0.00049983
  0.00059441 0.00070878 0.00009909 0.00019239 0.00026425 0.00057669
  0.00068087 0.13416073 0.003736   0.03724418 0.00007194 0.00159504
  0.02432369 0.19616836 0.00032401 0.0002351  0.0058203

INFO:tensorflow:loss = 3.7859898, step = 5001 (44.548 sec)
INFO:tensorflow:global_step/sec: 2.24886
INFO:tensorflow:probabilities = [[0.00647224 0.00032953 0.00357448 0.00047404 0.00258862 0.03108076
  0.0015548  0.00375791 0.00460919 0.00107619 0.02321541 0.00134673
  0.00020704 0.00006055 0.00014198 0.00118121 0.00241032 0.00006994
  0.0028477  0.0010131  0.39917034 0.00070244 0.01251623 0.00441276
  0.01394594 0.01486438 0.00548062 0.00043391 0.0334764  0.00421681
  0.00022369 0.00164297 0.01393346 0.00238208 0.00401871 0.00019051
  0.03350132 0.00091161 0.00114081 0.0699403  0.01151207 0.00044478
  0.00075969 0.00040226 0.02426345 0.0031508  0.00070405 0.00086446
  0.00020329 0.00022898 0.00436348 0.00102043 0.00014929 0.00437728
  0.0006958  0.00131738 0.00020043 0.04344396 0.00018188 0.00027111
  0.00288432 0.03519561 0.00017743 0.00209148 0.00048614 0.00105508
  0.0008365  0.00856937 0.00387015 0.0037245  0.00017062 0.00373546
  0.00147911 0.00095466 0.00582675 0.00041951 0.0003

INFO:tensorflow:loss = 3.8562334, step = 5101 (44.324 sec)
INFO:tensorflow:global_step/sec: 2.47787
INFO:tensorflow:probabilities = [[0.00254644 0.00296864 0.013716   0.01506942 0.0163756  0.01324358
  0.00518837 0.00709916 0.01947672 0.00665535 0.00932737 0.00637568
  0.00803978 0.0111152  0.00574375 0.01289324 0.00886598 0.00269458
  0.00773929 0.01066871 0.01446801 0.01644311 0.01066307 0.00247421
  0.00570043 0.01038919 0.00743093 0.02274201 0.01991365 0.00845993
  0.00396738 0.01487821 0.00772412 0.01259411 0.00674872 0.0071311
  0.00971171 0.00604577 0.01430977 0.01386242 0.0104901  0.01260505
  0.01657561 0.00876662 0.01557375 0.00583756 0.01574992 0.00342008
  0.01699499 0.0025036  0.00782455 0.01424473 0.00485734 0.00140044
  0.00652584 0.0309202  0.00674233 0.00412802 0.01315821 0.00332501
  0.00225967 0.00734302 0.00184967 0.01691507 0.0162188  0.01217605
  0.0259131  0.00885007 0.00420699 0.00729686 0.001645   0.00237892
  0.01179765 0.00710141 0.01294457 0.0150407  0.00612

INFO:tensorflow:loss = 3.7562246, step = 5201 (40.355 sec)
INFO:tensorflow:Saving checkpoints for 5240 into /tmp/cifar100/model.ckpt.
INFO:tensorflow:Loss for final step: 3.6274018.
Instructions for updating:
Switch to tf.estimator.Exporter and associated utilities.
Instructions for updating:
Switch to tf.estimator.Exporter and associated utilities.
Instructions for updating:
Switch to tf.estimator.Exporter and associated utilities.


TypeError: Failed to convert object of type <class 'dict'> to Tensor. Contents: {'seal': <tf.Tensor 'ParseExample/ParseExample:72' shape=(?, 1) dtype=float32>, 'oak': <tf.Tensor 'ParseExample/ParseExample:52' shape=(?, 1) dtype=float32>, 'house': <tf.Tensor 'ParseExample/ParseExample:38' shape=(?, 1) dtype=float32>, 'beetle': <tf.Tensor 'ParseExample/ParseExample:7' shape=(?, 1) dtype=float32>, 'castle': <tf.Tensor 'ParseExample/ParseExample:17' shape=(?, 1) dtype=float32>, 'ray': <tf.Tensor 'ParseExample/ParseExample:67' shape=(?, 1) dtype=float32>, 'crocodile': <tf.Tensor 'ParseExample/ParseExample:28' shape=(?, 1) dtype=float32>, 'lion': <tf.Tensor 'ParseExample/ParseExample:43' shape=(?, 1) dtype=float32>, 'maple': <tf.Tensor 'ParseExample/ParseExample:47' shape=(?, 1) dtype=float32>, 'leopard': <tf.Tensor 'ParseExample/ParseExample:42' shape=(?, 1) dtype=float32>, 'shrew': <tf.Tensor 'ParseExample/ParseExample:74' shape=(?, 1) dtype=float32>, 'cockroach': <tf.Tensor 'ParseExample/

In [35]:
test_model(classifier)

infer
infer
INFO:tensorflow:Starting evaluation at 2018-08-03-06:27:22
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/cifar100/model.ckpt-33528
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-08-03-06:27:27
INFO:tensorflow:Saving dict for global step 33528: accuracy = 0.424, global_step = 33528, loss = 2.4908679
{'global_step': 33528, 'loss': 2.4908679, 'accuracy': 0.424}
infer
infer
INFO:tensorflow:Starting evaluation at 2018-08-03-06:27:31
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/cifar100/model.ckpt-33528
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-08-03-06:27:36
INFO:tensorflow:Saving dict for global step 33528: accuracy = 0.442, global_step = 33528, loss = 2.2866387
{'global_step': 33528, 'loss': 2.2866387, 'accuracy': 0.442}
infer
infer
INFO:t

{'global_step': 33528, 'loss': 2.2949243, 'accuracy': 0.448}
infer
infer
INFO:tensorflow:Starting evaluation at 2018-08-03-06:28:53
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/cifar100/model.ckpt-33528
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-08-03-06:28:56
INFO:tensorflow:Saving dict for global step 33528: accuracy = 0.448, global_step = 33528, loss = 2.304841
{'global_step': 33528, 'loss': 2.304841, 'accuracy': 0.448}
infer
infer
INFO:tensorflow:Starting evaluation at 2018-08-03-06:28:58
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/cifar100/model.ckpt-33528
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-08-03-06:29:01
INFO:tensorflow:Saving dict for global step 33528: accuracy = 0.42, global_step = 33528, loss = 2.4275591
{'global_step': 33528